In [1]:
import plotly.express as px
import allel
import numpy as np
import pandas as pd

import warnings
warnings.filterwarnings('ignore')

def vcf_to_snp_dataframe(vcf_path, metadata):
    import ampseekertools as amp

    geno, pos, contig, metadata, ref, alt, ann = amp.load_vcf(vcf_path=vcf_path, metadata=metadata)
    
    # make dataframe of variant positions and merge with bed
    snp_df = pd.DataFrame({'contig':contig, 'pos':pos, 'ref':ref, 'alt':[list(a[a != ""]) for a in alt], 'ann':ann})

    snp_df = snp_df.explode('alt').reset_index().rename(columns={'index':'variant_index'})
    snp_df = snp_df.assign(alt_index=snp_df.groupby('pos').cumcount() + 1) 
    snp_df = snp_df.assign(label=lambda x: x.pos.astype(str) + " | " +  x.alt.fillna('NA'))
    snp_df.head(2)

    # split and find correct annotation 
    df = snp_df.assign(ann=lambda x: x.ann.str.split(","))
    anns = []
    for i, row in df.iterrows():
        alt = row['alt']
        if row['ann'] == None:
            ann = ""
        else:
            # keep only RD Vgsc annotations
            if 'AGAP004707' in ','.join(row['ann']):
                row['ann'] = [a for a in row['ann'] if "AGAP004707-RD" in a]

            ann = ','.join([a for a in row['ann'] if a.startswith(alt)])
        anns.append(ann)

    snp_df = snp_df.assign(ann=anns)
    
    return snp_df, geno

def calculate_frequencies_cohort(snp_df, metadata, geno, cohort_col, af_filter, missense_filter):
    np.seterr(all="ignore")
    
    df = snp_df.copy()
    
    # get indices of each cohort
    coh_dict = {}
    cohs = metadata[cohort_col].unique()
    cohs = cohs[~pd.isnull(cohs)]
    for coh in cohs:
        coh_dict[coh] = np.where(metadata[cohort_col] == coh)[0]
    
    # get allele counts for each population
    ac = geno.count_alleles_subpops(coh_dict, max_allele=3)
    
    for coh in cohs:
        total_counts = []
        alt_counts = []
        for i, row in df.iterrows():
            var_idx = row['variant_index']
            alt_idx = row['alt_index']
            total_counts.append(ac[coh][var_idx,:].sum())
            alt_counts.append(ac[coh][var_idx, alt_idx])

        df.loc[:, f'count_{coh}'] = np.array(alt_counts)
        df.loc[:, f'frq_{coh}'] = np.round(np.array(alt_counts)/np.array(total_counts), 3)
    
    freq_df = df.set_index('label').filter(like='frq')
    
    ann_df = snp_df.ann.str.split("|", expand=True).iloc[:, :11].drop(columns=[0,7,8])
    ann_df.columns = ['type', 'effect', 'gene', 'geneID', 'modifier', 'transcript', 'base_change', 'aa_change']
    snp_df = pd.concat([snp_df[['contig', 'pos', 'ref', 'alt']], ann_df], axis=1)
    snp_freq_df = pd.concat([snp_df, freq_df.reset_index()], axis=1)

    snp_freq_df = snp_freq_df.assign(label=
                  lambda x: x.contig + " | " + x.gene + " | " + x.pos.astype(str) + " | " + x.aa_change.str.replace("p.", "") + " | " + x.alt.fillna(" ")
                 )
    
    if af_filter:
        af_pass = (snp_freq_df.filter(like='frq') > 0.05).any(axis=1)
        snp_freq_df = snp_freq_df[af_pass]
    
    if missense_filter:
        snp_freq_df = snp_freq_df.query("type == 'missense_variant'")
    
    return snp_freq_df.set_index('label')

def plot_allele_frequencies(df, cohort_col, colscale="Reds"):
        
    fig = px.imshow(
            img=df,
            zmin=0,
            zmax=1,
            width=np.max([800, df.shape[1] * 100]),
            height=200 + (df.shape[0] * 18),
            text_auto=True,
            aspect=1,
            color_continuous_scale=colscale,
            title=f"Allele frequencies | by {cohort_col}",
        template='simple_white'
        )
    fig.update(layout_coloraxis_showscale=False)

    return fig 

In [2]:
dataset = 'ag-vampir-002'
metadata_path = "../../results/config/metadata.qcpass.tsv"
cohort_cols = 'location'
bed_path = "../../config/ag-vampir.bed"
vcf_path = "../../results/vcfs/targets/ag-vampir-002.annot.vcf"
wkdir = "../.."

In [3]:
# Parameters
metadata_path = "results/config/metadata.qcpass.tsv"
dataset = "ag-vampir-002"
wkdir = "/home/snagi/lstm_projects/ampseq-agvampir002"
bed_path = "config/ag-vampir.bed"
cohort_cols = "location,taxon"
vcf_path = "results/vcfs/targets/ag-vampir-002.annot.vcf"


In [4]:
import sys
import os
sys.path.append(os.path.join(wkdir, 'workflow'))
import ampseekertools as amp

### Plotting allele frequencies

This page shows allele frequencies in each cohort of the SNPs genotyped in the amplicon sequencing protocol.

In [5]:
cohort_cols = cohort_cols.split(",")

df_bed = pd.read_csv(bed_path, sep="\t", header=None, names=['contig', 'start', 'end', 'amplicon_id', 'mutation', 'ref', 'alt'])

# load metadata
if metadata_path.endswith('.xlsx'):
    metadata = pd.read_excel(metadata_path, engine='openpyxl')
elif metadata_path.endswith('.tsv'):
    metadata = pd.read_csv(metadata_path, sep="\t")
elif metadata_path.endswith('.csv'):
    metadata = pd.read_csv(metadata_path, sep=",")
else:
    raise ValueError("Metadata file must be .xlsx or .csv")

In [6]:
non_aim_snps = df_bed.query("~mutation.str.contains('AIM')").end.to_numpy()
snp_df, geno = vcf_to_snp_dataframe(vcf_path, metadata)

frq_dfs = []
for cohort_col in cohort_cols:
    
    freq_df = calculate_frequencies_cohort(
        snp_df=snp_df, 
        metadata=metadata,
        geno=geno, 
        cohort_col=cohort_col,
        af_filter=0.02,
        missense_filter=False
    )

    freq_df['contig'] = pd.Categorical(freq_df['contig'], categories=['2R', '2L', '3R', '3L', 'X'], ordered=True)
    freq_df = freq_df.sort_values(by=['contig', 'pos'])
    freq_df = freq_df.query("gene ! = 'para' and pos in @non_aim_snps")
    frq_dfs.append(freq_df.reset_index(drop=True))

    fig = plot_allele_frequencies(
        df=freq_df.filter(like='frq_'),
        cohort_col=cohort_col,
        colscale="Reds"
    )

    # hm = freq_df.filter(like='frq_').reset_index()
    # for i in range(len(hm.columns)):
    #     fig.add_shape(type="line", x0=0.5 + i, y0=-0.5, x1=0.5 + i, y1=len(hm.index) - 0.5, line=dict(color="grey", width=1))

    # for i in np.arange(len(hm.index)):
    #     if i == 22:
    #         continue
    #     fig.add_shape(type="line", x0=-0.5, y0=0.5 + i, x1=len(hm.columns) - 0.5, y1=0.5 + i, line=dict(color="grey", width=1))

    #fig.write_image(f"{wkdir}/results/allele_frequencies_{cohort_col}_novgsc.png", scale=2)
    fig.show()

#### SNP frequency summary table

In [7]:
pd.set_option("display.max_rows", 200)
pd.set_option('display.max_columns', 100)

snp_df = pd.concat([snp_df] + frq_dfs, axis=1)
snp_df.to_csv(f"{wkdir}/results/snp_frequencies_summary.tsv", sep="\t")
snp_df

variant_index contig       pos ref  alt  \
0                0     2R   3492074   G    A   
1                1     2R   8368731   A    C   
2                2     2R  17854287   C    A   
3                3     2R  28492879   A    G   
4                4     2R  28494247   C    T   
5                5     2R  28497563   T    C   
6                6     2R  28497967   G    C   
7                6     2R  28497967   G    A   
8                7     2R  28498192   C  NaN   
9                8     2R  28499661   G    T   
10               9     2R  28500643   G  NaN   
11              10     2R  28501399   G    A   
12              10     2R  28501399   G    T   
13              11     2R  28502736   C    A   
14              12     2R  28502850   C    T   
15              13     2R  48714551   A  NaN   
16              14     2R  48714601   A  NaN   
17              15     2R  49438586   T    C   
18              16     3R     34264   A    G   
19              17     3R     35121   A    G   
20              18     3R     38161   A    G   
21              19     3R     42848   A    C   
22              20     3R     50590   T    G   
23              21     3R     71973   C    A   
24              21     3R     71973   C    G   
25              22     3R     97617   G    A   
26              23     3R   8564156   G    A   
27              24     3R  28592158   G  NaN   
28              25     3R  28595449   C    T   
29              26     3R  28598057   G    A   
30              26     3R  28598057   G    C   
31              27     3R  28598062   G    C   
32              28     3R  28598166   A    G   
33              29     3R  28600701   A    G   
34              30     2L    209536   G    A   
35              30     2L    209536   G    C   
36              31     2L    927247   A    C   
37              32     2L   1274353   A    G   
38              33     2L   1418210   C    T   
39              34     2L   1571929   C    T   
40              35     2L   1776348   C    G   
41              36     2L   1947574   A    G   
42              37     2L   2380982   T    C   
43              38     2L   2381706   A  NaN   
44              39     2L   2388595   G  NaN   
45              40     2L   2391228   G  NaN   
46              41     2L   2399997   G    A   
47              42     2L   2403941   T    A   
48              42     2L   2403941   T    C   
49              43     2L   2408423   C  NaN   
50              44     2L   2408677   A  NaN   
51              45     2L   2414062   A    G   
52              46     2L   2416980   C    T   
53              47     2L   2422651   T    C   
54              48     2L   2422652   A    T   
55              49     2L   2425052   G    A   
56              50     2L   2425766   T    C   
57              51     2L   2429617   T    C   
58              52     2L   2429745   A    T   
59              53     2L   2429897   A    G   
60              54     2L   2430424   G    T   
61              55     2L   2430817   G    A   
62              55     2L   2430817   G    C   
63              56     2L   2430863   T    C   
64              57     2L   2430880   C    T   
65              58     2L   2430881   C    T   
66              59     2L   2431005   C    T   
67              60     2L   2431061   C  NaN   
68              61     2L   2432419   T    G   
69              62     2L   2435581   G    A   
70              63     2L  20288132   T    C   
71              64     2L  25429235   G    T   
72              65     2L  25429236   C    G   
73              65     2L  25429236   C    T   
74              66     2L  25635973   G    A   
75              67     2L  34073195   C  NaN   
76              68     2L  34100758   A    T   
77              68     2L  34100758   A    G   
78              69     2L  34118141   G    A   
79              70     2L  34118260   G    A   
80              71     3L     65133   G    T   
81              72     3L    129051   A    C   
82              73   

#### Allele frequencies of any SNPs across amplicons

In [8]:
vcf_path = f"{wkdir}/results/vcfs/amplicons/{dataset}.annot.vcf"
cohort_col = cohort_cols[0]

snp_df, geno = vcf_to_snp_dataframe(vcf_path, metadata)

snp_freq_df = calculate_frequencies_cohort(
    snp_df=snp_df, 
    metadata=metadata,
    geno=geno, 
    cohort_col=cohort_col, 
    af_filter=0.05,
    missense_filter=True
)   

snp_freq_df = snp_freq_df.filter(like='frq')
snp_freq_df.columns = snp_freq_df.columns.str.replace("frq_", "")

plot_allele_frequencies(
    df=snp_freq_df,
    cohort_col=cohort_col
)